In [2]:
import sys
sys.path.append("../scripts/")
from ideal_robot import *
from scipy.stats import expon, norm

In [3]:
class Robot(IdealRobot):

    def __init__(self, pose, agent=None, sensor=None, color="black",
                 noise_per_meter=5, # 1[m]あたりの小石の数(5個）
                 noise_std=math.pi/60, # 小石を踏んだときにロボットの向きシータ[deg]に発生する雑音の標準偏差(3[deg])
                 bias_rate_stds=(0.1, 0.1) # バイアスの係数をドローするためのガウス分布の標準偏差(速度、角速度）
                ): 
        super().__init__(pose, agent, sensor, color) # 派生IdealRobotのメソッドを呼び出すときに使う関数super()
        self.noise_pdf = expon(scale=1.0/(1e-100 + noise_per_meter)) # 指数分布のオブジェクトnoise_pdfを生成する。scale：小石を踏むまでの平均の道のり(1/ラムダ）
        self.distance_until_noise = self.noise_pdf.rvs() # 最初に小石を踏むまでの道のりをセット。rvs()はRandomVariableSの略でランダム変数の生成。
        self.theta_noise = norm(scale=noise_std) # シータに加える雑音を決めるためのガウス分布のオブジェクトを生成
        self.bias_rate_nu = norm.rvs(loc=1.0, scale=bias_rate_stds[0]) # loc: 平均
        self.bias_rate_omega = norm.rvs(loc=1.0, scale=bias_rate_stds[1])
    
    def noise(self, pose, nu, omega, time_interval):
        self.distance_until_noise -= abs(nu) * time_interval + self.r * abs(omega) * time_interval # 次に小石を踏むまでの道のりdistance_until_noiseを経過時間分だけ減らす
        if self.distance_until_noise <= 0.0: # ゼロ以下なら小石を踏んだ
            self.distance_until_noise += self.noise_pdf.rvs() # 小石を踏んだら次の小石を踏むまでの道のりをセット
            pose[2] += self.theta_noise.rvs() # シータに雑音を加える

        return pose

    def bias(self, nu, omega):
        return nu * self.bias_rate_nu, omega * self.bias_rate_omega
    
    def one_step(self, time_interval):
        if not self.agent: return
        obs = self.sensor.data(self.pose) if self.sensor else None
        nu, omega = self.agent.decision(obs)
        nu, omega = self.bias(nu, omega)
        self.pose = self.state_transition(nu, omega, time_interval, self.pose)
        self.pose = self.noise(self.pose, nu, omega, time_interval) # ノイズを実行する

In [7]:
import copy

world = World(30, 0.1)

circling = Agent(0.2, 10.0/180*math.pi)

nobias_robot = IdealRobot( np.array([0, 0, 0]).T, sensor=None, agent=circling, color="gray")
world.append(nobias_robot)

bias_robot = Robot( np.array([0, 0, 0]).T, sensor=None, agent=circling, color="red",
                   noise_per_meter=0, bias_rate_stds=(0.2, 0.2))
world.append(bias_robot)

world.draw()